In [1]:
import pathlib
import glob
import re
import os
import pprint

In [2]:
root = pathlib.Path('datas')
pdfList = glob.glob('datas/**/*.pdf', recursive=True)
print(pdfList)
print(type(pdfList))

['datas\\ジェスクホリウチ\\20200612110726.pdf', 'datas\\テクノハンズ\\TUT157-101\u3000XDT70-105型.PDF', 'datas\\テクノハンズ\\_TD-102 UART Command Reference Manual V008_141006.pdf', 'datas\\テクノハンズ\\_TD-102_PC Manager Manual_V208_141006.pdf', 'datas\\テクノハンズ\\_TD-102_Technical description_V104_140610.pdf', 'datas\\テクノワシノ\\20200612115521.pdf', 'datas\\テクノワシノ\\20200612115540.pdf', 'datas\\テクノワシノ\\20200612115558.pdf', 'datas\\ユアサ工機\\20200612114054.pdf', 'datas\\ユアサ工機\\20200612114448.pdf', 'datas\\ユアサ工機\\20200612114547.pdf', 'datas\\ユアサ工機\\20200612114612.pdf', 'datas\\ワシノエンジニアリング\\20200612115647.pdf', 'datas\\ワシノエンジニアリング\\20200612115701.pdf', 'datas\\ワシノエンジニアリング\\20200612115719.pdf', 'datas\\ワシノエンジニアリング\\20200612115735.pdf', 'datas\\ワシノエンジニアリング\\20200612115750.pdf', 'datas\\ワシノエンジニアリング\\20200612115808.pdf', 'datas\\ワシノエンジニアリング\\20200612115850.pdf', 'datas\\ワシノエンジニアリング\\20200612120008.pdf', 'datas\\ワシノエンジニアリング\\20200612120113.pdf', 'datas\\ワシノエンジニアリング\\20200612120235.pdf', 'datas\\ワシノエンジニアリング\\20200612120358.pdf'

In [3]:
tifList = glob.glob('datas/**/*.tif', recursive=True)
print(tifList)

[]


In [4]:
#Tesseract OCR パス通し
path_tesseract = "C:\\Program Files (x86)\\Tesseract-OCR"
if path_tesseract not in os.environ["PATH"].split(os.pathsep):
    os.environ["PATH"] += os.pathsep + path_tesseract

In [5]:
#pdfの画像変換ライブラリインストール
!pip install pdf2image
!pip show pdf2image

Name: pdf2image
Version: 1.13.1
Summary: A wrapper around the pdftoppm and pdftocairo command line tools to convert PDF to a PIL Image list.
Home-page: https://github.com/Belval/pdf2image
Author: Edouard Belval
Author-email: edouard@belval.org
License: MIT
Location: c:\users\11bigstone\anaconda3\envs\pyocr\lib\site-packages
Requires: pillow
Required-by: 


In [6]:
#popのPath通し
poppler_path = os.path.join(os.getcwd(), "poppler-0.68.0", "bin")
os.environ["PATH"] += os.pathsep + poppler_path

In [7]:
#OCR依存ライブラリ群
from PIL import Image
import sys
import pyocr
import pyocr.builders

In [8]:
#pyOCR動作確認
tools = pyocr.get_available_tools()
if len(tools) == 0:
    print("OCR tool is not found")
    sys.exit(1)

tool = tools[0]
print("OCR tool is '%s'" % (tool.get_name()))

OCR tool is 'Tesseract (sh)'


In [9]:
#pyOCR動作言語確認
langs = tool.get_available_languages()
print("Available languages: %s" % ", ".join(langs))
lang = langs[0]
print("Will use lang '%s'" % (lang))

Available languages: eng, jav, jpn, jpn_vert, osd, script/Arabic, script/Armenian, script/Bengali, script/Canadian_Aboriginal, script/Cherokee, script/Cyrillic, script/Devanagari, script/Ethiopic, script/Fraktur, script/Georgian, script/Greek, script/Gujarati, script/Gurmukhi, script/HanS, script/HanS_vert, script/HanT, script/HanT_vert, script/Hangul, script/Hangul_vert, script/Hebrew, script/Japanese, script/Japanese_vert, script/Kannada, script/Khmer, script/Lao, script/Latin, script/Malayalam, script/Myanmar, script/Oriya, script/Sinhala, script/Syriac, script/Tamil, script/Telugu, script/Thaana, script/Thai, script/Tibetan, script/Vietnamese
Will use lang 'eng'


In [10]:
#pdf画像化処理に必要なライブラリ群のインポート
import os
from pathlib import Path
from pdf2image import convert_from_path

#Mecab
import MeCab
import os
from pathlib import Path
import codecs

In [11]:
for i in range(0,len(pdfList)):
    # PDFファイルのパス
    pdf_path = pdfList[i];
    print("----------" + pdf_path + "----------" +"(" + str(i) + "/" + str(len(pdfList)) + ")");

    # PDF -> Image に変換
    pages = convert_from_path(str(pdf_path), 400);

    path = str(pdf_path).split('.');
    txt = '';
    image_dir = path[0];
    
    os.makedirs(str(image_dir), exist_ok=True)
    for i, page in enumerate(pages):
        file_name = "{:02d}".format(i + 1) + ".jpeg"
        image_path = image_dir + '/' + file_name
        # JPEGで保存
        print("save: " + image_path)
        page.save(str(image_path), "JPEG")
        files = os.listdir(image_dir)
        files.sort()
        fileNum = "{:02d}".format(i + 1)
        print(files)
    #画像ページ送りfor
    for i in range(0, len(files)):
        txtPath = files[i]
        #OCR処理
        txt = txt + tool.image_to_string(
        Image.open(image_dir + '/' + txtPath),
        lang="jpn",
        builder=pyocr.builders.TextBuilder(tesseract_layout=6)
      )
    txt = txt.replace(' ', '')
    txt = txt.replace('　', '')
    tagger = MeCab.Tagger()
    analyzed = tagger.parse(txt)
    print(analyzed)
    with open(image_dir+ ".txt", mode='w') as f:
        f.write(analyzed)

----------datas\ジェスクホリウチ\20200612110726.pdf----------(0/41)
save: datas\ジェスクホリウチ\20200612110726/01.jpeg
['01.jpeg']
save: datas\ジェスクホリウチ\20200612110726/02.jpeg
['01.jpeg', '02.jpeg']
save: datas\ジェスクホリウチ\20200612110726/03.jpeg
['01.jpeg', '02.jpeg', '03.jpeg']
save: datas\ジェスクホリウチ\20200612110726/04.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg']
save: datas\ジェスクホリウチ\20200612110726/05.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg']
save: datas\ジェスクホリウチ\20200612110726/06.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg']
save: datas\ジェスクホリウチ\20200612110726/07.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg']
save: datas\ジェスクホリウチ\20200612110726/08.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg']
NR	名詞,一般,*,*,*,*,*
0220002292	名詞,数,*,*,*,*,*
が	助詞,格助詞,一般,*,*,*,が,ガ,ガ
2	名詞,数,*,*,*,*,*
NR	名詞,一般,*,*,*,*,*
22	名詞,数,*,*,*,*,*
ツン	副詞,助詞類接続,*,*,*,*,ツン,ツン,ツン
7	名詞,数,*,*,*,*,*
。	記号,句点,*,*,*,*

save: datas\テクノハンズ\TUT157-101　XDT70-105型/01.jpeg
['01.jpeg']
パャュエュエエニョハニニョニョ	名詞,一般,*,*,*,*,*
べべ	名詞,一般,*,*,*,*,べべ,ベベ,ベベ
つ	助動詞,*,*,*,下二・タ行,基本形,つ,ツ,ツ
べ	助詞,終助詞,*,*,*,*,べ,ベ,ベ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
べべ	名詞,一般,*,*,*,*,べべ,ベベ,ベベ
つ	助動詞,*,*,*,下二・タ行,基本形,つ,ツ,ツ
べ	助詞,終助詞,*,*,*,*,べ,ベ,ベ
|	名詞,サ変接続,*,*,*,*,*
20	名詞,数,*,*,*,*,*
10	名詞,数,*,*,*,*,*
.	名詞,サ変接続,*,*,*,*,*
22	名詞,数,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
15	名詞,数,*,*,*,*,*
吐通	名詞,一般,*,*,*,*,*
二	名詞,数,*,*,*,*,二,ニ,ニ
<	名詞,サ変接続,*,*,*,*,*
87	名詞,数,*,*,*,*,*
|	名詞,サ変接続,*,*,*,*,*
1	名詞,数,*,*,*,*,*
」	記号,括弧閉,*,*,*,*,」,」,」
キーゴー	名詞,一般,*,*,*,*,*
「	記号,括弧開,*,*,*,*,「,「,「
59	名詞,数,*,*,*,*,*
レー	名詞,一般,*,*,*,*,*
1	名詞,数,*,*,*,*,*
|	名詞,サ変接続,*,*,*,*,*
インーー	名詞,一般,*,*,*,*,*
|	名詞,サ変接続,*,*,*,*,*
旧	接頭詞,名詞接続,*,*,*,*,旧,キュウ,キュー
目	名詞,一般,*,*,*,*,目,メ,メ
目	名詞,接尾,一般,*,*,*,目,メ,メ
目	名詞,接尾,一般,*,*,*,目,メ,メ
間	名詞,接尾,一般,*,*,*,間,カン,カン
目	名詞,接尾,一般,*,*,*,目,メ,メ
目	名詞,接尾,一般,*,*,

['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg']
save: datas\テクノハンズ\_TD-102 UART Command Reference Manual V008_141006/07.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg']
save: datas\テクノハンズ\_TD-102 UART Command Reference Manual V008_141006/08.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg']
save: datas\テクノハンズ\_TD-102 UART Command Reference Manual V008_141006/09.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg', '09.jpeg']
save: datas\テクノハンズ\_TD-102 UART Command Reference Manual V008_141006/10.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg', '09.jpeg', '10.jpeg']
save: datas\テクノハンズ\_TD-102 UART Command Reference Manual V008_141006/11.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg', '09.jpeg', '10.jpeg', '11.jpeg']
ぐる	名詞,一般,*,*,*,*,ぐる,グル,グル
p	名詞,一般,*,*,*,*,*
テクノハ

save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/01.jpeg
['01.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/02.jpeg
['01.jpeg', '02.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/03.jpeg
['01.jpeg', '02.jpeg', '03.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/04.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/05.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/06.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/07.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/08.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg']
save: datas\テクノハンズ\_TD-102_PC Manager Manual_V208_141006/09.jpeg
['01.jpeg',

save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/01.jpeg
['01.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/02.jpeg
['01.jpeg', '02.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/03.jpeg
['01.jpeg', '02.jpeg', '03.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/04.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/05.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/06.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/07.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg']
save: datas\テクノハンズ\_TD-102_Technical description_V104_140610/08.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg', '06.jpeg', '07.jpeg', '08.jpeg']
save: datas\テクノハンズ\_TD-102_Technical descrip

...

save: datas\西部自動機器\20200612115047/01.jpeg
['01.jpeg']
save: datas\西部自動機器\20200612115047/02.jpeg
['01.jpeg', '02.jpeg']
save: datas\西部自動機器\20200612115047/03.jpeg
['01.jpeg', '02.jpeg', '03.jpeg']
save: datas\西部自動機器\20200612115047/04.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg']
save: datas\西部自動機器\20200612115047/05.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg', '05.jpeg']
EsAEROLIDE	名詞,固有名詞,組織,*,*,*,*
"	名詞,サ変接続,*,*,*,*,*
P	名詞,一般,*,*,*,*,*
9	名詞,数,*,*,*,*,*
_	名詞,サ変接続,*,*,*,*,*
gg	名詞,一般,*,*,*,*,*
4	名詞,数,*,*,*,*,*
局	名詞,接尾,助数詞,*,*,*,局,キョク,キョク
条	名詞,接尾,助数詞,*,*,*,条,ジョウ,ジョー
25	名詞,数,*,*,*,*,*
区	名詞,接尾,助数詞,*,*,*,区,ク,ク
sa	名詞,固有名詞,組織,*,*,*,*
人	名詞,接尾,一般,*,*,*,人,ジン,ジン
論	名詞,接尾,一般,*,*,*,論,ロン,ロン
7	名詞,数,*,*,*,*,*
/	名詞,サ変接続,*,*,*,*,*
6	名詞,数,*,*,*,*,*
還	動詞,自立,*,*,五段・ラ行,体言接続特殊２,還る,カエ,カエ
_	名詞,サ変接続,*,*,*,*,*
4	名詞,数,*,*,*,*,*
肖	動詞,自立,*,*,五段・ラ行,体言接続特殊２,肖る,アヤカ,アヤカ
|	名詞,サ変接続,*,*,*,*,*
ル	名詞,一般,*,*,*,*,*
kb	名詞,一般,*,*,*,*,*
7	名詞,数,*,*,*,*,*
『	記号,括弧開,*,*,*,*,『,『,『
り	助動詞,*,*,*,文語・リ,基本形,り,リ,リ
/	名詞,サ変接続,*,*,*,*,*
届	

save: datas\西部自動機器\20200612115147/01.jpeg
['01.jpeg']
save: datas\西部自動機器\20200612115147/02.jpeg
['01.jpeg', '02.jpeg']
save: datas\西部自動機器\20200612115147/03.jpeg
['01.jpeg', '02.jpeg', '03.jpeg']
save: datas\西部自動機器\20200612115147/04.jpeg
['01.jpeg', '02.jpeg', '03.jpeg', '04.jpeg']
ーー	名詞,一般,*,*,*,*,*
*~	名詞,サ変接続,*,*,*,*,*
ン	名詞,非自立,一般,*,*,*,ン,ン,ン
ア	名詞,一般,*,*,*,*,*
<$	名詞,サ変接続,*,*,*,*,*
Ss	名詞,一般,*,*,*,*,*
<	名詞,サ変接続,*,*,*,*,*
em	名詞,一般,*,*,*,*,*
_	名詞,サ変接続,*,*,*,*,*
7	名詞,数,*,*,*,*,*
ーー	名詞,一般,*,*,*,*,*
で	助詞,格助詞,一般,*,*,*,で,デ,デ
ーー	名詞,一般,*,*,*,*,*
較直	名詞,一般,*,*,*,*,*
仕上	動詞,自立,*,*,五段・ラ行,体言接続特殊２,仕上る,シアガ,シアガ
機	名詞,接尾,一般,*,*,*,機,キ,キ
の	助詞,連体化,*,*,*,*,の,ノ,ノ
加	名詞,固有名詞,地域,国,*,*,加,カ,カ
エノウハウ	名詞,一般,*,*,*,*,*
を	助詞,格助詞,一般,*,*,*,を,ヲ,ヲ
提供	名詞,サ変接続,*,*,*,*,提供,テイキョウ,テイキョー
プ	名詞,一般,*,*,*,*,*
4	名詞,数,*,*,*,*,*
,	名詞,サ変接続,*,*,*,*,*
000	名詞,数,*,*,*,*,*
FP	名詞,一般,*,*,*,*,*
央	名詞,固有名詞,人名,名,*,*,央,ヒサシ,ヒサシ
る	助動詞,*,*,*,文語・リ,体言接続,り,ル,ル
ション	名詞,固有名詞,人名,名,*,*,ション,ション,ション
で	助動詞,*,*,*,特殊・ダ,連用形,だ,デ,デ
高	接頭詞,名詞接続,*,*,*,*,高,コウ,コー
能率	名詞,一般,*,*

save: datas\西部自動機器\20200612115310/01.jpeg
['01.jpeg']
save: datas\西部自動機器\20200612115310/02.jpeg
['01.jpeg', '02.jpeg']
EiAEROLIDE	名詞,固有名詞,組織,*,*,*,*
"	名詞,サ変接続,*,*,*,*,*
pu	名詞,一般,*,*,*,*,*
拉	名詞,一般,*,*,*,*,*
2	名詞,数,*,*,*,*,*
t	名詞,一般,*,*,*,*,*
径超	名詞,一般,*,*,*,*,*
仕上	動詞,自立,*,*,五段・ラ行,体言接続特殊２,仕上る,シアガ,シアガ
紫	名詞,一般,*,*,*,*,紫,ムラサキ,ムラサキ
ASM	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
500	名詞,数,*,*,*,*,*
ZR	名詞,一般,*,*,*,*,*
T	名詞,一般,*,*,*,*,*
h	名詞,一般,*,*,*,*,*
r	名詞,一般,*,*,*,*,*
oughFeedSystemCenterlessO	名詞,一般,*,*,*,*,*
.	名詞,サ変接続,*,*,*,*,*
D	名詞,一般,*,*,*,*,*
.	名詞,サ変接続,*,*,*,*,*
StoneLappingMachineModel	名詞,一般,*,*,*,*,*
:	名詞,サ変接続,*,*,*,*,*
ASM	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
500	名詞,数,*,*,*,*,*
ZR	名詞,一般,*,*,*,*,*
IE	名詞,一般,*,*,*,*,*
ニー	名詞,一般,*,*,*,*,*
に	助詞,格助詞,一般,*,*,*,に,ニ,ニ
EEiESpapsamrID	名詞,一般,*,*,*,*,*
3	名詞,数,*,*,*,*,*
e	名詞,一般,*,*,*,*,*
5	名詞,数,*,*,*,*,*
CE	名詞,一般,*,*,*,*,*
六	名詞,数,*,*,*,*,六,ロク,ロク
har	名詞,一般,*,*,*,*,*
デーニニーーテーュー	名詞,一般,*,*,*,*,*
NE	名詞,一般,*,*,*,*,*
了	名詞,固有名詞,人名,名,*,*,了,リョウ,リョー
/	名詞,サ変接続,*,*,*,*,*


save: datas\西部自動機器\20200612115335/01.jpeg
['01.jpeg']
save: datas\西部自動機器\20200612115335/02.jpeg
['01.jpeg', '02.jpeg']
ErimAEROLIDE	名詞,固有名詞,組織,*,*,*,*
汎用	名詞,一般,*,*,*,*,汎用,ハンヨウ,ハンヨー
超	接頭詞,名詞接続,*,*,*,*,超,チョウ,チョー
仕	動詞,自立,*,*,五段・ラ行,体言接続特殊２,仕る,ツカマツ,ツカマツ
上角	名詞,一般,*,*,*,*,上角,ウエスミ,ウエスミ
CN	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
35	名詞,数,*,*,*,*,*
ONC	名詞,一般,*,*,*,*,*
馬	名詞,接尾,一般,*,*,*,馬,バ,バ
General	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
p	名詞,一般,*,*,*,*,*
urboseStoneLappingMachine	名詞,一般,*,*,*,*,*
,	名詞,サ変接続,*,*,*,*,*
In	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
FeedModel	名詞,一般,*,*,*,*,*
:	名詞,サ変接続,*,*,*,*,*
CN	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
350	名詞,数,*,*,*,*,*
NC	名詞,一般,*,*,*,*,*
矯	名詞,一般,*,*,*,*,*
SECRETE	名詞,一般,*,*,*,*,*
2	名詞,数,*,*,*,*,*
EE	名詞,一般,*,*,*,*,*
9222	名詞,数,*,*,*,*,*
SRKSSORGCESEUyDY	名詞,一般,*,*,*,*,*
0	名詞,数,*,*,*,*,*
RZ	名詞,一般,*,*,*,*,*
ス	名詞,一般,*,*,*,*,*
SAGEEYGSOPST	名詞,一般,*,*,*,*,*
の	名詞,非自立,一般,*,*,*,の,ノ,ノ
と	助詞,並立助詞,*,*,*,*,と,ト,ト
SEEEISTERT	名詞,固有名詞,組織,*,*,*,*
て	助詞,格助詞,連語,*,*,*,て,テ,テ
OO	名詞,固有名詞,組織,*,*,*

save: datas\西部自動機器\20200612115354/01.jpeg
['01.jpeg']
save: datas\西部自動機器\20200612115354/02.jpeg
['01.jpeg', '02.jpeg']
EsAEROLIDE	名詞,固有名詞,組織,*,*,*,*
"	名詞,サ変接続,*,*,*,*,*
旋藻	名詞,一般,*,*,*,*,*
球面	名詞,一般,*,*,*,*,球面,キュウメン,キューメン
超	接頭詞,名詞接続,*,*,*,*,超,チョウ,チョー
仕	動詞,自立,*,*,五段・ラ行,体言接続特殊２,仕る,ツカマツ,ツカマツ
上角	名詞,一般,*,*,*,*,上角,ウエスミ,ウエスミ
HN	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
500	名詞,数,*,*,*,*,*
CO	名詞,一般,*,*,*,*,*
中	名詞,接尾,副詞可能,*,*,*,中,チュウ,チュー
Was	名詞,固有名詞,組織,*,*,*,*
C	名詞,一般,*,*,*,*,*
e	名詞,一般,*,*,*,*,*
n	名詞,一般,*,*,*,*,*
t	名詞,一般,*,*,*,*,*
e	名詞,一般,*,*,*,*,*
r	名詞,一般,*,*,*,*,*
l	名詞,一般,*,*,*,*,*
e	名詞,一般,*,*,*,*,*
s	名詞,一般,*,*,*,*,*
s	名詞,一般,*,*,*,*,*
S	名詞,一般,*,*,*,*,*
p	名詞,一般,*,*,*,*,*
h	名詞,一般,*,*,*,*,*
e	名詞,一般,*,*,*,*,*
r	名詞,一般,*,*,*,*,*
i	名詞,一般,*,*,*,*,*
c	名詞,一般,*,*,*,*,*
a	名詞,一般,*,*,*,*,*
l	名詞,一般,*,*,*,*,*
S	名詞,一般,*,*,*,*,*
u	名詞,一般,*,*,*,*,*
r	名詞,一般,*,*,*,*,*
f	名詞,一般,*,*,*,*,*
a	名詞,一般,*,*,*,*,*
c	名詞,一般,*,*,*,*,*
eStoneLappingMachineModel	名詞,一般,*,*,*,*,*
:	名詞,サ変接続,*,*,*,*,*
RN	名詞,一般,*,*,*,*,*
-	名詞,サ変接続,*,*,*,*,*
50

In [12]:
for i in range(0,len(pdfList)):
    # tifファイルのパス
    tif_path = tifList[i];
    print("------------------------------" + tif_path + "(" + str(i) + "/" + str(len(tifList)) + ")");

    # tif -> Image に変換
    pages = convert_from_path(str(tif_path), 400);

    path = str(tif_path).split('.');
    txt = '';
    image_dir = path[0];
    
    os.makedirs(str(image_dir), exist_ok=True)
    for i, page in enumerate(pages):
        file_name = "{:02d}".format(i + 1) + ".jpeg"
        image_path = image_dir + '/' + file_name
        # JPEGで保存
        print("save: " + image_path)
        page.save(str(image_path), "JPEG")
        files = os.listdir(image_dir)
        files.sort()
        fileNum = "{:02d}".format(i + 1)
        print(files)
    #画像ページ送りfor
    for i in range(0, len(files)):
        txtPath = files[i]
        #OCR処理
        txt = txt + tool.image_to_string(
        Image.open(image_dir + '/' + txtPath),
        lang="jpn",
        builder=pyocr.builders.TextBuilder(tesseract_layout=6)
      )
    txt = txt.replace(' ', '')
    txt = txt.replace('　', '')
    tagger = MeCab.Tagger()
    analyzed = tagger.parse(txt)
    print(analyzed)
    with open(image_dir+ ".txt", mode='w') as f:
        f.write(analyzed)

IndexError: list index out of range